In [1]:
import altair as alt
import pandas as pd
import numpy as np
import streamlit as st
from vega_datasets import data as vega_data
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [2]:
data = pd.read_csv('./Global Economy Indicators.csv')

# data.info()
data.columns = data.columns.str.strip()
rename_rules = {
    'CountryID': 'country_id',  # 国家的唯一标识符
    'Country': 'country',  # 国家名称
    'Year': 'year',  # 年份
    'AMA exchange rate': 'ama_exchange_rate',  # AMA汇率
    'IMF based exchange rate': 'imf_exchange_rate',  # 基于IMF的汇率
    'Population': 'population',  # 人口数量
    'Currency': 'currency',  # 使用的货币
    'Per capita GNI': 'per_capita_gni',  # 人均国民总收入
    'Agriculture, hunting, forestry, fishing (ISIC A-B)': 'agr_hunt_forest_fish_gva',  # 农业、狩猎、林业、渔业产值
    'Changes in inventories': 'changes_in_inventories',  # 存货变动
    'Construction (ISIC F)': 'construction_gva',  # 建筑业产值
    'Exports of goods and services': 'exports',  # 商品和服务出口总额
    'Final consumption expenditure': 'final_consumption_expenditure',  # 最终消费支出
    'General government final consumption expenditure': 'gov_final_consumption_expenditure',  # 政府最终消费支出
    'Gross capital formation': 'gross_capital_formation',  # 固定资本形成总额
    'Gross fixed capital formation (including Acquisitions less disposals of valuables)': 'gross_fixed_capital_formation',  # 固定资本形成净额
    'Household consumption expenditure (including Non-profit institutions serving households)': 'household_consumption_expenditure',  # 家庭消费支出
    'Imports of goods and services': 'imports',  # 商品和服务进口总额
    'Manufacturing (ISIC D)': 'manufacturing_gva',  # 制造业产值
    'Mining, Manufacturing, Utilities (ISIC C-E)': 'mining_manufacturing_utilities_gva',  # 采矿业、制造业和公共事业产值
    'Other Activities (ISIC J-P)': 'other_activities_gva',  # 其他活动产值
    'Total Value Added': 'total_value_added',  # 总增加值
    'Transport, storage and communication (ISIC I)': 'transport_storage_comm_gva',  # 运输、仓储和通信业产值
    'Wholesale, retail trade, restaurants and hotels (ISIC G-H)': 'wholesale_retail_trade_gva',  # 批发和零售贸易、餐饮和酒店业产值
    'Gross National Income(GNI) in USD': 'gni_usd',  # 以美元计的国民总收入
    'Gross Domestic Product (GDP)': 'gdp'  # 国内生产总值
}

df = data.rename(columns=rename_rules)
print(df.columns)
df.info()

Index(['country_id', 'country', 'year', 'ama_exchange_rate',
       'imf_exchange_rate', 'population', 'currency', 'per_capita_gni',
       'agr_hunt_forest_fish_gva', 'changes_in_inventories',
       'construction_gva', 'exports', 'final_consumption_expenditure',
       'gov_final_consumption_expenditure', 'gross_capital_formation',
       'gross_fixed_capital_formation', 'household_consumption_expenditure',
       'imports', 'manufacturing_gva', 'mining_manufacturing_utilities_gva',
       'other_activities_gva', 'total_value_added',
       'transport_storage_comm_gva', 'wholesale_retail_trade_gva', 'gni_usd',
       'gdp'],
      dtype='object')
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 10512 entries, 0 to 10511
Data columns (total 26 columns):
 #   Column                              Non-Null Count  Dtype  
---  ------                              --------------  -----  
 0   country_id                          10512 non-null  int64  
 1   country                           

In [3]:
print(df[['country_id','country', 'year','gdp']].head(100))
print(df['country_id'].dtype)
print(df['year'].dtype)

    country_id        country  year           gdp
0            4   Afghanistan   1970  1.731436e+09
1            4   Afghanistan   1971  1.812838e+09
2            4   Afghanistan   1972  1.647900e+09
3            4   Afghanistan   1973  1.702716e+09
4            4   Afghanistan   1974  2.061729e+09
..         ...            ...   ...           ...
95           8       Albania   2013  1.277628e+10
96           8       Albania   2014  1.322824e+10
97           8       Albania   2015  1.138692e+10
98           8       Albania   2016  1.186136e+10
99           8       Albania   2017  1.301973e+10

[100 rows x 4 columns]
int64
int64


In [4]:
df['country_id'] = df['country_id'].astype(str)
df['year'] = df['year'].astype(int)
df_small = df[['country_id', 'gdp', 'year']]

world_geojson = vega_data.world_110m.url
world = alt.topo_feature(world_geojson, 'countries')

year = st.slider('Year', min_value=df['year'].min(), max_value=df['year'].max(), step=1)

# 使用滑动条的值来筛选数据
df_filtered = df[df['year'] == year]
# 创建地图
chart = alt.Chart(world).mark_geoshape().encode(
    alt.Color('gdp:Q', scale=alt.Scale(scheme="blueorange"), title="GDP")
).transform_lookup(
    lookup='id',
    from_=alt.LookupData(df_filtered, 'country_id', ['gdp'])
).project(
    type='equalEarth'
).properties(
    width=700,
    height=400,
    title=f'Global GDP Map for {year}'
)

# 在 Streamlit 中显示地图
st.altair_chart(chart)


2024-03-30 20:08:20.349 WARNING streamlit.runtime.state.session_state_proxy: Session state does not function when running a script without `streamlit run`
2024-03-30 20:08:20.819 
  command:

    streamlit run c:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py [ARGUMENTS]


DeltaGenerator(_root_container=0, _provided_cursor=None, _parent=None, _block_type=None, _form_data=None)

In [5]:
# 确保 country_id 是字符串类型
df['country_id'] = df['country_id'].astype(str)

# 打印出能够匹配上的country_id列表
print(df['country_id'].unique())

# 检查GDP列是否含有NaN值
print(df['gdp'].isnull().sum())

# 创建一个包含转换结果的新图表，并打印输出
lookup_chart = alt.Chart(world).transform_lookup(
    lookup='id',
    from_=alt.LookupData(df, 'country_id', ['gdp'])
).mark_geoshape()

# 查看转换后的数据
lookup_data = lookup_chart.to_dict()

# 打印转换后的数据（这里可能需要进一步的代码来正确打印完整的转换结果）
print(lookup_data)


['4' '8' '12' '20' '24' '28' '31' '32' '36' '40' '44' '48' '50' '51' '52'
 '56' '60' '64' '68' '70' '72' '76' '84' '90' '92' '96' '100' '104' '108'
 '112' '116' '120' '124' '132' '136' '140' '144' '148' '152' '156' '170'
 '174' '178' '180' '184' '188' '191' '192' '196' '200' '203' '204' '208'
 '212' '214' '218' '222' '226' '230' '231' '232' '233' '242' '246' '250'
 '258' '262' '266' '268' '270' '275' '276' '288' '296' '300' '304' '308'
 '320' '324' '328' '332' '340' '344' '348' '352' '356' '360' '364' '368'
 '372' '376' '380' '384' '388' '392' '398' '400' '404' '408' '410' '412'
 '414' '417' '418' '422' '426' '428' '430' '434' '438' '440' '442' '446'
 '450' '454' '458' '462' '466' '470' '478' '480' '484' '492' '496' '498'
 '499' '500' '504' '508' '512' '516' '520' '524' '528' '530' '531' '533'
 '534' '540' '548' '554' '558' '562' '566' '578' '583' '584' '585' '586'
 '591' '598' '600' '604' '608' '616' '620' '624' '626' '630' '634' '642'
 '643' '646' '659' '660' '662' '670' '674' '678' 

: 